[View in Colaboratory](https://colab.research.google.com/github/vivek09pathak/Ml_Detects/blob/master/Ship_Detector_14-Aug.ipynb)

In [0]:
import tensorflow as tf
import numpy as np
import os
import sys
import time
import cv2
import math  
from collections import defaultdict
from io import StringIO
from matplotlib import pyplot as plt
from PIL import Image


In [64]:
cd Ml_Detects/object_detection/

/content/Ml_Detects/object_detection


In [22]:
# Here are the imports from the object detection module.
from object_detection.utils import label_map_util
from object_detection.utils import visualization_utils as vis_util

/content/models/research/object_detection/utils/visualization_utils.py:25: UserWarning: 
This call to matplotlib.use() has no effect because the backend has already
been chosen; matplotlib.use() must be called *before* pylab, matplotlib.pyplot,
or matplotlib.backends is imported for the first time.

The backend was *originally* set to 'module://ipykernel.pylab.backend_inline' by the following code:
  File "/usr/lib/python3.6/runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "/usr/lib/python3.6/runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py", line 16, in <module>
    app.launch_new_instance()
  File "/usr/local/lib/python3.6/dist-packages/traitlets/config/application.py", line 657, in launch_instance
    app.initialize(argv)
  File "<decorator-gen-121>", line 2, in initialize
  File "/usr/local/lib/python3.6/dist-packages/traitlets/config/application.py", line 87, in catch_confi

In [65]:
# Model preparation
MODEL_NAME = './export_models/ssd_mobilenet_v1_ship_15000'
print(MODEL_NAME)

# Path to frozen detection graph. This is the actual model that is used for the object detection.
PATH_TO_CKPT = MODEL_NAME + '/frozen_inference_graph.pb'
print(PATH_TO_CKPT)
# List of the strings that is used to add correct label for each box.
PATH_TO_LABELS = os.path.join('./data', 'ship_label_map.pbtxt')
print(PATH_TO_LABELS)
NUM_CLASSES = 1


./export_models/ssd_mobilenet_v1_ship_15000
./export_models/ssd_mobilenet_v1_ship_15000/frozen_inference_graph.pb
./data/ship_label_map.pbtxt


In [70]:
cd ..

/content


In [0]:
# Load a (frozen) Tensorflow model into memory.
detection_graph = tf.Graph()
with detection_graph.as_default():
  od_graph_def = tf.GraphDef()
  with tf.gfile.GFile(r'./export_models/ssd_mobilenet_v1_ship_15000/frozen_inference_graph.pb', 'rb') as fid:
    serialized_graph = fid.read()
    od_graph_def.ParseFromString(serialized_graph)
    tf.import_graph_def(od_graph_def, name='')


In [0]:
label_map = label_map_util.load_labelmap(PATH_TO_LABELS)
categories = label_map_util.convert_label_map_to_categories(label_map, max_num_classes=NUM_CLASSES, use_display_name=True)
category_index = label_map_util.create_category_index(categories)

In [0]:
def load_image_into_numpy_array(image):
  (im_width, im_height) = [500,500]
  return np.array(image.getdata()).reshape(
      (im_height, im_width, 3)).astype(np.uint8)


In [0]:

def calculateDistance(x1,y1,x2,y2):  
    dist = math.sqrt((x2 - x1)**2 + (y2 - y1)**2) 
    delta =0.0033 * (dist**2) -1.9918 * dist +372.28
    
    return delta  


In [0]:
def pipeline(image):
  
    with detection_graph.as_default():
          with tf.Session(graph=detection_graph) as sess:
                
                image_np = np.asarray(image)
                image_np_expanded = np.expand_dims(image_np, axis=0)
                image_tensor = detection_graph.get_tensor_by_name('image_tensor:0')
                # Each box represents a part of the image where a particular object was detected.
                boxes = detection_graph.get_tensor_by_name('detection_boxes:0')
                # Each score represent how level of confidence for each of the objects.
                # Score is shown on the result image, together with the class label.
                scores = detection_graph.get_tensor_by_name('detection_scores:0')

                classes = detection_graph.get_tensor_by_name('detection_classes:0')
                num_detections = detection_graph.get_tensor_by_name('num_detections:0')
                # Actual detection.
                (boxes, scores, classes, num_detections) = sess.run(
                  [boxes, scores, classes, num_detections],
                  feed_dict={image_tensor: image_np_expanded})
                # Visualization of the results of a detection.
                vis_util.visualize_boxes_and_labels_on_image_array(
                  image_np,
                  np.squeeze(boxes),
                  np.squeeze(classes).astype(np.int32),
                  np.squeeze(scores),
                  category_index,
                  use_normalized_coordinates=True,
                  min_score_thresh=.9,
                  line_thickness=2)
                
                ################### Data analysis ###################
                print("")
                final_score = np.squeeze(scores)  # scores
                r_count = 0  # counting
                r_score = []  # temp score, <class 'numpy.ndarray'>
                final_category = np.array([category_index.get(i) for i in classes[0]]) # category
                r_category = np.array([])  # temp category

                for i in range(100):
                    if scores is None or final_score[i] > 0.7:
                        r_count = r_count + 1
                        r_score = np.append(r_score, final_score[i])
                        r_category = np.append(r_category, final_category[i])

                if r_count > 0:
                    print("Number of bounding boxes: ", r_count)
                    print("")
                else:
                    print("Not Detect")
                    print("")
                for i in range(len(r_score)):  # socre array`s length
                    print("Object Num: {} , Category: {} , Score: {}%".format(i+1, r_category[i]['name'], 100*r_score[i]))
                    print("")
                    final_boxes = np.squeeze(boxes)[i]  # ymin, xmin, ymax, xmax
                    xmin = final_boxes[1]
                    ymin = final_boxes[0]
                    xmax = final_boxes[3]
                    ymax = final_boxes[2]
                    location_x = (xmax+xmin)/2
                    location_y = (ymax+ymin)/2
                    min_location=location_y*100
                    
                    # print("final_boxes [ymin xmin ymax xmax]")
                    # print("final_boxes", final_boxes)
                    if(min_location>35):
                      cv2.putText(image_np,'FAR', (100, 90),  cv2.FONT_HERSHEY_SIMPLEX,1.5, (0,255,0), thickness=2)
                    else:
                      cv2.putText(image_np,'NEAR' , (100, 90),  cv2.FONT_HERSHEY_SIMPLEX,1.5, (255,0,0), thickness=2)
                    print("Location x: {}, y: {}".format(location_x, location_y))
                    print("")
                print("+ " * 30 ) 
               
    return image_np

                



In [144]:

from moviepy.editor import VideoFileClip
vid_output = 'result9_1.mp4'
clip = VideoFileClip("test.mp4")
vid = clip.fl_image(pipeline)
vid.write_videofile(vid_output, audio=False)


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 95.5794632434845%

Location x: 0.33327627182006836, y: 0.40351414680480957

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 
[MoviePy] >>>> Building video result9_1.mp4
[MoviePy] Writing video result9_1.mp4












  0%|          | 0/398 [00:00<?, ?it/s]









  0%|          | 1/398 [00:01<07:23,  1.12s/it]


Not Detect

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 












  1%|          | 2/398 [00:02<07:08,  1.08s/it]


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 94.43159699440002%

Location x: 0.3330706059932709, y: 0.40283888578414917

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 


...


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 91.99538826942444%

Location x: 0.9014461040496826, y: 0.4608324468135834

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 












100%|█████████▉| 397/398 [07:18<00:01,  1.10s/it]


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 82.91129469871521%

Location x: 0.8968379497528076, y: 0.4653843939304352

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 












100%|██████████| 398/398 [07:19<00:00,  1.10s/it]












Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 97.92630076408386%

Location x: 0.894199788570404, y: 0.4791402220726013

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 
[MoviePy] Done.
[MoviePy] >>>> Video ready: result9_1.mp4 



In [145]:

import io# import # import 
import base64
from IPython.display import HTML

video = io.open('result9_1.mp4', 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video alt="test" controls>
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii')))

In [71]:
cd Ship-Detector/

/content/Ship-Detector


In [61]:
!git clone https://github.com/tensorflow/tensorflow

Cloning into 'tensorflow'...
remote: Counting objects: 401973, done.
remote: Compressing objects: 100% (16/16), done.
remote: Total 401973 (delta 4), reused 6 (delta 2), pack-reused 401955
Receiving objects: 100% (401973/401973), 184.53 MiB | 15.15 MiB/s, done.
Resolving deltas: 100% (319768/319768), done.


In [64]:
cd tools/graph_transforms/

/content/Ship-Detector/tensorflow/tensorflow/tools/graph_transforms


In [73]:
!bazel build tensorflow/tools/graph_transforms:transform_graph

/bin/sh: 1: bazel: not found


In [31]:
!pip install moviepy

    100% |████████████████████████████████| 378kB 24.2MB/s 
    100% |████████████████████████████████| 3.3MB 6.8MB/s 
    100% |████████████████████████████████| 51kB 17.2MB/s 
  Running setup.py bdist_wheel for moviepy ... - \ | done
  Stored in directory: /content/.cache/pip/wheels/ad/92/4d/a6c6307d4c2219d002646bd4a5987e31fd5697f6ea7778b2c0
Successfully built moviepy


In [72]:
ls

api/         compatibility/    gcs_test/          mlpbtxt/       test/
benchmark/   def_file_filter/  git/               pip_package/
build_info/  dist_test/        graph_transforms/  proto_text/
ci_build/    docker/           __init__.py        quantization/
common/      docs/             lib_package/       swig/


In [71]:
!python freeze_graph.py

python3: can't open file 'freeze_graph.py': [Errno 2] No such file or directory
